### Imports

In [1]:
import pandas as pd
from datetime import timedelta
from datetime import datetime as dt
import datetime
import yfinance as yf
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.model_selection import train_test_split, cross_val_score, StratifiedKFold
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import RandomizedSearchCV
from imblearn.over_sampling import ADASYN
from xgboost import XGBClassifier
import xgboost as xgb
import pytz
from sklearn.preprocessing import MinMaxScaler
from imblearn.over_sampling import BorderlineSMOTE
from sklearn.decomposition import PCA
from sklearn.metrics import roc_auc_score
from sklearn.feature_selection import SelectFromModel
import tensorflow as tf
from tensorflow import keras
from keras import layers, callbacks
from sklearn.utils.class_weight import compute_class_weight
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.pipeline import Pipeline
from tensorflow.keras.optimizers.legacy import Adam
from tensorflow.keras.layers import Dense, BatchNormalization, Dropout
from tensorflow.keras.regularizers import l2
from sklearn.ensemble import VotingClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.tree import DecisionTreeClassifier
from keras.models import Sequential
import keras_tuner as kt
from kerastuner.tuners import RandomSearch
import joblib
import itertools
import lightgbm as lgb

/var/folders/zc/z8rbpqpj3s38f0x8wmhkq0lh0000gn/T/ipykernel_61088/3810277901.py:39: DeprecationWarning: `import kerastuner` is deprecated, please use `import keras_tuner`.
  from kerastuner.tuners import RandomSearch


### Helper Functions

In [2]:
def next_four_fridays():
    # Get today's date and time in EST timezone
    est = pytz.timezone('US/Eastern')
    today = dt.now(est)
    
    # Find the next Friday
    days_until_friday = (4 - today.weekday() + 7) % 7
    next_friday = today + timedelta(days=days_until_friday)
    
    # Reset the time to 4:30 PM on the next Friday
    next_friday = next_friday.replace(hour=16, minute=30, second=0, microsecond=0)
    
    # If today is Friday and it's past 4:30 PM, consider the next week's Friday
    if today.weekday() == 4 and today.time() > next_friday.time():
        next_friday += timedelta(days=7)
    
    # Remove time from datetime for output
    next_friday = next_friday.date()
    
    # Find the Friday after the next
    following_friday = next_friday + timedelta(days=7)
    
    # Find the Friday after the following
    next_next_friday = following_friday + timedelta(days=7)
    
    # Find the Friday after the next next
    next_next_next_friday = next_next_friday + timedelta(days=7)
    
    return next_friday.strftime('%Y-%m-%d'), following_friday.strftime('%Y-%m-%d'), next_next_friday.strftime('%Y-%m-%d'), next_next_next_friday.strftime('%Y-%m-%d')

# Get the next four Fridays
friday1, friday2, friday3, friday4 = next_four_fridays()
print(f"The next four Fridays are: {friday1}, {friday2}, {friday3}, and {friday4}")

The next four Fridays are: 2023-10-27, 2023-11-03, 2023-11-10, and 2023-11-17


# Viewing option chains

In [4]:
print(friday1)

2023-10-27


In [5]:
file_viewer = pd.read_csv('Data/naked_puts_results.csv')
filtered_data = file_viewer[file_viewer['Expiration Date'] == friday1]

# Display all rows, no limit
pd.set_option('display.max_rows', None)
# Display all columns, no limit
pd.set_option('display.max_columns', None)

filtered_data['ROI (%)'] = filtered_data['ROI (%)'].astype(float)
# filter out rows with ROI (%) greater than 0.8
# filtered_data = filtered_data[filtered_data['ROI (%)'] > 0.8]
# filter out rows with strike price less than 6
# filtered_data = filtered_data[filtered_data['strike'] <= 7]

# sort by ROI (%) in ascending order
filtered_data = filtered_data.sort_values(by=['ROI (%)'], ascending=False)

# Show only the columns 'Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)', 'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', and '52WeekLow'
filtered_data = filtered_data[['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)',
    'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', '52WeekLow']]

# Show only the top 10 rows
filtered_data.head(20)

Expiration Date   ETF  Stock Price   bid  strike  ROI (%)  OTM (%)  \
104      2023-10-27  SNAP         9.44  0.72     9.0     8.70     4.66   
121      2023-10-27    WE         2.05  0.15     2.0     8.11     2.44   
21       2023-10-27   CGC         0.51  0.03     0.5     6.38     1.96   
103      2023-10-27  SNAP         9.44  0.48     8.5     5.99     9.96   
62       2023-10-27  NKLA         1.02  0.05     1.0     5.26     1.96   
60       2023-10-27   MPW         4.70  0.22     4.5     5.14     4.26   
12       2023-10-27   AMC         9.08  0.44     9.0     5.14     0.88   
61       2023-10-27  MVIS         2.01  0.09     2.0     4.71     0.50   
88       2023-10-27    QS         5.84  0.24     5.5     4.56     5.82   
111      2023-10-27  SPWR         5.09  0.20     5.0     4.17     1.77   
83       2023-10-27  PLUG         6.10  0.22     6.0     3.81     1.64   
102      2023-10-27  SNAP         9.44  0.29     8.0     3.76    15.25   
75       2023-10-27  PACW         7.35  0.25     7.0     3.70     4.76   
118      2023-10-27   TUP         1.72  0.05     1.5     3.45    12.79   
13       2023-10-27  APLD         4.69  0.15     4.5     3.45     4.05   
74       2023-10-27  PACW         7.35  0.20     6.5     3.17    11.56   
1        2023-10-27  AAOI         6.91  0.20     6.5     3.17     5.93   
89       2023-10-27  RDFN         5.07  0.15     5.0     3.09     1.38   
16       2023-10-27  AVXL         5.20  0.15     5.0     3.09     3.85   
11       2023-10-27   AMC         9.08  0.24     8.5     2.91     6.39   

     Implied Volatility  volume  openInterest  highPrice  \
104                1.71  2426.0        4439.0       0.72   
121                1.88    60.0         319.0       0.15   
21                 1.38   296.0        2879.0       0.03   
103                1.66  1646.0       13223.0       0.48   
62                 1.09  1013.0       23774.0       0.05   
60                 1.16  3912.0        4226.0       0.22   
12                 0.91  7266.0        5760.0       0.44   
61                 0.97   100.0         273.0       0.09   
88                 1.17   278.0        1239.0       0.24   
111                0.87   169.0         180.0       0.20   
83                 0.76   975.0         713.0       0.22   
102                1.60  2552.0        6904.0       0.29   
75                 1.13    11.0          32.0       0.25   
118                1.72    45.0         134.0       0.05   
13                 0.95    85.0         519.0       0.15   
74                 1.34    77.0       10784.0       0.20   
1                  1.00     6.0          20.0       0.20   
89                 0.79    32.0         117.0       0.15   
16                 0.96    17.0         110.0       0.15   
11                 0.93  2996.0        6204.0       0.24   

     Original Stock Price  Original ROI (%)  Original OTM (%)  50-day MA  \
104                  9.44              8.70              4.66       9.25   
121                  2.05              8.11              2.44       3.91   
21                   0.51              6.38              1.96       0.72   
103                  9.44              5.99              9.96       9.25   
62                   1.02              5.26              1.96       1.35   
60                   4.70              5.14              4.26       6.07   
12                   9.08              5.14              0.88      14.02   
61                   2.01              4.71              0.50       2.33   
88                   5.84              4.56              5.82       6.70   
111                  5.09              4.17              1.77       6.55   
83                   6.10              3.81              1.64       7.87   
102                  9.44              3.76             15.25       9.25   
75                   7.35              3.70              4.76       7.84   
118                  1.72              3.45             12.79       2.13   
13                   4.69              3.45     

In [6]:
# Read in data
df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Define function to color rows 
def color_row(row):
    color = 'lightgreen' if row['Status'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Filter columns to keep
columns = ['ETF', 'Original Stock Price', 'Stock Price', 'strike', 'volume',  
           'openInterest', 'highPrice', 'Original ROI (%)', 'Original OTM (%)',
           '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP',
           '52WeekHigh', '52WeekLow', 'Status']

# Take top 100 rows ordered by Original ROI (%)
df = df[columns].sort_values('Original ROI (%)', ascending=False).head(100)

# Style DataFrame 
styled_df = (df.style  
             .applymap(lambda x: 'color: black') # Set text color
             .apply(color_row, axis=1) # Set row colors
             .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns))

# Display DataFrame 
styled_df

In [7]:
# Load the CSV file into a DataFrame
df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Data Preprocessing
# Drop any columns that are not relevant for prediction
df.drop(['contractSymbol', 'Expiration Date', 'ETF'], axis=1, inplace=True)

# Encode categorical variables using one-hot encoding
df = pd.get_dummies(df, columns=['recommendationKey'], drop_first=True)

# Handle missing values with imputation
from sklearn.impute import SimpleImputer
imputer = SimpleImputer(strategy='mean')
X = df.drop('Status', axis=1)
y = df['Status']

# Encode the target variable 'Status'
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

X_imputed = imputer.fit_transform(X)

# Address class imbalance with SMOTE
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X_imputed, y_encoded)

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

# Model Selection and Hyperparameter Tuning (LightGBM)
param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [3, 4, 5],
    'learning_rate': [0.05, 0.1, 0.2]
}

# Use GridSearchCV for hyperparameter tuning
lgb_classifier = lgb.LGBMClassifier(random_state=42)
grid_search = GridSearchCV(lgb_classifier, param_grid, cv=10, scoring='accuracy', n_jobs=-1)
grid_search.fit(X_train, y_train)

best_lgb_model = grid_search.best_estimator_

# Model Evaluation
y_pred = best_lgb_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
report = classification_report(y_test, y_pred)

print(f'Best LightGBM Model: {best_lgb_model}')
print(f'Accuracy: {accuracy}')
print(report)


import joblib

# Dump the label_encoder to a file
label_encoder_filename = "label_encoder.joblib"
joblib.dump(label_encoder, label_encoder_filename)

# Save the trained LightGBM model and scaler to separate files
model_filename = "model.joblib"
scaler_filename = "scaler.joblib"

joblib.dump(best_lgb_model, model_filename)
joblib.dump(imputer, scaler_filename)

# Making Predictions on New Data
# Load the new data
new_data = pd.read_csv("Data/naked_puts_results.csv")

# Make a copy of the new data for predictions
new_data_with_predictions = new_data.copy()

# Apply the same preprocessing steps as before
# Drop columns not relevant for prediction
new_data.drop(['contractSymbol', 'Expiration Date', 'ETF'], axis=1, inplace=True)

# Encode categorical variables using one-hot encoding
new_data = pd.get_dummies(new_data, columns=['recommendationKey'], drop_first=True)

# Handle missing values with imputation
imputer = SimpleImputer(strategy='mean')
new_X_imputed = imputer.fit_transform(new_data)  # No need to drop 'Status'

# Load the label encoder
label_encoder = joblib.load("label_encoder.joblib")

# Load the trained LightGBM model
best_lgb_model = joblib.load("model.joblib")

# Make predictions on the new data
new_predictions = best_lgb_model.predict(new_X_imputed)

# Convert numerical predictions back to labels ("Success" or "Failed")
new_predictions_labels = label_encoder.inverse_transform(new_predictions)

# Add predictions to the new data
new_data_with_predictions["Guess"] = new_predictions_labels

# Save the new data with predictions, including 'contractSymbol', 'Expiration Date', and 'ETF'
new_data_with_predictions.to_csv("Data/new_data_with_predictions.csv", index=False)

[LightGBM] [Info] Number of positive: 542, number of negative: 524
[LightGBM] [Info] Number of positive: 542, number of negative: 525
[LightGBM] [Info] Number of positive: 542, number of negative: 524
[LightGBM] [Info] Number of positive: 541, number of negative: 525
[LightGBM] [Info] Number of positive: 541, number of negative: 525
[LightGBM] [Info] Number of positive: 542, number of negative: 524
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002646 seconds.
You can set `force_col_wise=true` to remove the overhead.[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004818 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.

[LightGBM] [Info] Total Bins 8137
[LightGBM] [Info] Total Bins 8109
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003108 seconds.
You can set `force_col_wise=true` to r

In [8]:
# Read in data 
df = pd.read_csv('Data/new_data_with_predictions.csv')

# Sort by Original ROI column  
df = df.sort_values(by='Original ROI (%)', ascending=False)  

# Filter to top 300 rows
df = df.head(300)

# Filter columns to show
columns = ['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 
           'ROI (%)', 'OTM (%)', 'recommendationKey', 'targetLowPrice', 'targetMeanPrice', 'targetHighPrice', 'Guess']
df = df[columns]

# Define row color function
def color_row(row):
    color = 'lightgreen' if row['Guess'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Apply cell and row styling
styled_df = (df.style
                .applymap(lambda x: 'color: black') # Black text
                .apply(color_row, axis=1) # Color rows
                .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns)) 

# Display styled DataFrame
styled_df